## Assignment 08

### DSC650
Taniya Adhikari

In [8]:
import json
import uuid
import pandas as pd
import time

from kafka import KafkaProducer, KafkaAdminClient
from kafka.admin.new_topic import NewTopic
from kafka.errors import TopicAlreadyExistsError

### Configuration Parameters 

> **TODO:** Change the configuration prameters to the appropriate values for your setup.

In [9]:
config = dict(
    bootstrap_servers=['localhost:9092'],
    first_name='Taniya',
    last_name='Adhikari'
)

config['client_id'] = '{}{}'.format(
    config['last_name'], 
    config['first_name']
)
config['topic_prefix'] = '{}{}'.format(
    config['last_name'], 
    config['first_name']
)

config

{'bootstrap_servers': ['localhost:9092'],
 'first_name': 'Taniya',
 'last_name': 'Adhikari',
 'client_id': 'AdhikariTaniya',
 'topic_prefix': 'AdhikariTaniya'}

### Create Topic Utility Function

The `create_kafka_topic` helps create a Kafka topic based on your configuration settings.  For instance, if your first name is *John* and your last name is *Doe*, `create_kafka_topic('locations')` will create a topic with the name `DoeJohn-locations`.  The function will not create the topic if it already exists. 

In [10]:
KafkaProducer(bootstrap_servers=['localhost:9092'],
              api_version=(0,10,1),
              value_serializer=lambda x: dumps(x).encode('utf-8'))

In [11]:
def create_kafka_topic(topic_name, config=config, num_partitions=1, replication_factor=1):
    bootstrap_servers = config['bootstrap_servers']
    client_id = config['client_id']
    topic_prefix = config['topic_prefix']
    name = '{}-{}'.format(topic_prefix, topic_name)
    
    admin_client = KafkaAdminClient(
        bootstrap_servers=bootstrap_servers, 
        client_id=client_id
    )
    
    topic = NewTopic(
        name=name,
        num_partitions=num_partitions,
        replication_factor=replication_factor
    )

    topic_list = [topic]
    try:
        admin_client.create_topics(new_topics=topic_list)
        print('Created topic "{}"'.format(name))
    except TopicAlreadyExistsError as e:
        print('Topic "{}" already exists'.format(name))
    
create_kafka_topic('locations')
create_kafka_topic('accelerations')

Topic "AdhikariTaniya-locations" already exists
Topic "AdhikariTaniya-accelerations" already exists


### Kafka Producer

The following code creates a `KafkaProducer` object which you can use to send Python objects that are serialized as JSON.

**Note:** This producer serializes Python objects as JSON. This means that object must be JSON serializable.  As an example, Python `DateTime` values are not JSON serializable and must be converted to a string (e.g. ISO 8601) or a numeric value (e.g. a Unix timestamp) before being sent.

In [12]:
producer = KafkaProducer(
  bootstrap_servers=config['bootstrap_servers'],
  value_serializer=lambda x: json.dumps(x).encode('utf-8')
)

### Send Data Function

The `send_data` function sends a Python object to a Kafka topic. This function adds the `topic_prefix` to the topic so `send_data('locations', data)` sends a JSON serialized message to `DoeJohn-locations`. The function also registers callbacks to let you know if the message has been sent or if an error has occured. 

In [13]:
def on_send_success(record_metadata):
    print('Message sent:\n    Topic: "{}"\n    Partition: {}\n    Offset: {}'.format(
        record_metadata.topic,
        record_metadata.partition,
        record_metadata.offset
    ))
    
def on_send_error(excp):
    print('I am an errback', exc_info=excp)
    # handle exception

def send_data(topic, data, config=config, producer=producer, msg_key=None):
    topic_prefix = config['topic_prefix']
    topic_name = '{}-{}'.format(topic_prefix, topic)
    
    if msg_key is not None:
        key = msg_key
    else:
        key = uuid.uuid4().hex
    
    producer.send(
        topic_name, 
        value=data,
        key=key.encode('utf-8')
    ).add_callback(on_send_success).add_errback(on_send_error)

In [14]:
example_data = dict(
    key1='value1',
    key2='value2'
)

send_data('locations', example_data)
send_data('accelerations', example_data)

Message sent:
    Topic: "AdhikariTaniya-locations"
    Partition: 0
    Offset: 5
Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0
    Offset: 2


In [15]:
import os
from pathlib import Path
import pyarrow as pa
import pyarrow.parquet as pq

In [25]:
current_dir = Path(os.getcwd()).absolute()
current_dir = Path(current_dir).parents[2]
data_dir = current_dir.joinpath('data')
processed_dir = data_dir.joinpath('processed')
bdd_dir = processed_dir.joinpath('bdd')
locations_dir = bdd_dir.joinpath('locations')
accelerations_dir = bdd_dir.joinpath('accelerations')

### Publishing Locations and Accelerations Data

In [17]:
import pyarrow as pa
import pyarrow.parquet as pq

In [26]:
# loading locations data
locations = pd.read_parquet(locations_dir).sort_values('offset').reset_index()
# loading accelerations data
accelerations = pd.read_parquet(accelerations_dir).sort_values('offset').reset_index()

In [21]:
locations.head(2)

index                                id                           ride_id  \
0      1  85c61911b7fe2ced1000c33c9e932706  6760ffa3f41908695d1405b776c3e8d5   
1      0  58682c5d48cad9d9e103431d773615bf  c9a2b46c9aa515b632eddc45c4868482   

                               uuid                  timestamp    offset  \
0  dad7eae44e784b549c8c5a3aa051a8c7 1970-01-01 00:25:07.320453  1.077913   
1  19b9aa10588646b3bf22c9b4865a7995 1970-01-01 00:25:03.882586  1.525061   

       course   latitude  longitude       geohash  speed  accuracy  timelapse  \
0  158.203125  40.677641 -73.817930  dr5x2jpkmtcy   2.12      10.0      False   
1  299.619141  40.762870 -73.961949  dr5ruuwscttz   0.00      10.0      False   

                                   filename      t  
0  d745b92f-aefd-467d-9121-7a71308e8d6d.mov  000.0  
1  e2f795a7-6a7d-4500-b5d7-4569de996811.mov  000.0

In [27]:
accelerations.head(2)

index                                id                           ride_id  \
0      0  58682c5d48cad9d9e103431d773615bf  c9a2b46c9aa515b632eddc45c4868482   
1      1  58682c5d48cad9d9e103431d773615bf  c9a2b46c9aa515b632eddc45c4868482   

                               uuid                  timestamp    offset  \
0  19b9aa10588646b3bf22c9b4865a7995 1970-01-01 00:25:03.882586  0.822061   
1  19b9aa10588646b3bf22c9b4865a7995 1970-01-01 00:25:03.882586  0.842061   

       x      y      z  timelapse                                  filename  \
0 -0.994  0.045 -0.036      False  e2f795a7-6a7d-4500-b5d7-4569de996811.mov   
1 -0.998  0.046 -0.040      False  e2f795a7-6a7d-4500-b5d7-4569de996811.mov   

       t  
0  000.0  
1  000.0

In [22]:
locations.timestamp = locations.timestamp.dt.strftime('%Y-%m-%d %H:%M:%S.%f')
locations_dict = locations.to_dict(orient='records')
locations_dict[0]

{'index': 1,
 'id': '85c61911b7fe2ced1000c33c9e932706',
 'ride_id': '6760ffa3f41908695d1405b776c3e8d5',
 'uuid': 'dad7eae44e784b549c8c5a3aa051a8c7',
 'timestamp': '1970-01-01 00:25:07.320453',
 'offset': 1.0779125295566454,
 'course': 158.203125,
 'latitude': 40.677641336844,
 'longitude': -73.81793000742218,
 'geohash': 'dr5x2jpkmtcy',
 'speed': 2.119999885559082,
 'accuracy': 10.0,
 'timelapse': False,
 'filename': 'd745b92f-aefd-467d-9121-7a71308e8d6d.mov',
 't': '000.0'}

In [28]:
accelerations.timestamp = accelerations.timestamp.dt.strftime('%Y-%m-%d %H:%M:%S.%f')
accelerations_dict = accelerations.to_dict(orient='records')
accelerations_dict[0]

{'index': 0,
 'id': '58682c5d48cad9d9e103431d773615bf',
 'ride_id': 'c9a2b46c9aa515b632eddc45c4868482',
 'uuid': '19b9aa10588646b3bf22c9b4865a7995',
 'timestamp': '1970-01-01 00:25:03.882586',
 'offset': 0.8220608865228429,
 'x': -0.994,
 'y': 0.045,
 'z': -0.036000000000000004,
 'timelapse': False,
 'filename': 'e2f795a7-6a7d-4500-b5d7-4569de996811.mov',
 't': '000.0'}

In [24]:
# publishing locations data
last_offset = 0
for index,row in locations.iterrows():
    offset = row['offset']
    time.sleep(offset - last_offset)
    payload = locations_dict[index]
    send_data('locations', payload)
    last_offset = offset

Message sent:
    Topic: "AdhikariTaniya-locations"
    Partition: 0
    Offset: 7
Message sent:
    Topic: "AdhikariTaniya-locations"
    Partition: 0
    Offset: 8
Message sent:
    Topic: "AdhikariTaniya-locations"
    Partition: 0
    Offset: 9
Message sent:
    Topic: "AdhikariTaniya-locations"
    Partition: 0
    Offset: 10
Message sent:
    Topic: "AdhikariTaniya-locations"
    Partition: 0
    Offset: 11
Message sent:
    Topic: "AdhikariTaniya-locations"
    Partition: 0
    Offset: 12
Message sent:
    Topic: "AdhikariTaniya-locations"
    Partition: 0
    Offset: 13
Message sent:
    Topic: "AdhikariTaniya-locations"
    Partition: 0
    Offset: 14
Message sent:
    Topic: "AdhikariTaniya-locations"
    Partition: 0
    Offset: 15
Message sent:
    Topic: "AdhikariTaniya-locations"
    Partition: 0
    Offset: 16
Message sent:
    Topic: "AdhikariTaniya-locations"
    Partition: 0
    Offset: 17
Message sent:
    Topic: "AdhikariTaniya-locations"
    Partition: 0
    Offset

Message sent:
    Topic: "AdhikariTaniya-locations"
    Partition: 0
    Offset: 105
Message sent:
    Topic: "AdhikariTaniya-locations"
    Partition: 0
    Offset: 106
Message sent:
    Topic: "AdhikariTaniya-locations"
    Partition: 0
    Offset: 107
Message sent:
    Topic: "AdhikariTaniya-locations"
    Partition: 0
    Offset: 108
Message sent:
    Topic: "AdhikariTaniya-locations"
    Partition: 0
    Offset: 109
Message sent:
    Topic: "AdhikariTaniya-locations"
    Partition: 0
    Offset: 110
Message sent:
    Topic: "AdhikariTaniya-locations"
    Partition: 0
    Offset: 111
Message sent:
    Topic: "AdhikariTaniya-locations"
    Partition: 0
    Offset: 112
Message sent:
    Topic: "AdhikariTaniya-locations"
    Partition: 0
    Offset: 113
Message sent:
    Topic: "AdhikariTaniya-locations"
    Partition: 0
    Offset: 114
Message sent:
    Topic: "AdhikariTaniya-locations"
    Partition: 0
    Offset: 115
Message sent:
    Topic: "AdhikariTaniya-locations"
    Partition

    Offset: 205
Message sent:
    Topic: "AdhikariTaniya-locations"
    Partition: 0
    Offset: 206
Message sent:
    Topic: "AdhikariTaniya-locations"
    Partition: 0
    Offset: 207
Message sent:
    Topic: "AdhikariTaniya-locations"
    Partition: 0
    Offset: 208
Message sent:
    Topic: "AdhikariTaniya-locations"
    Partition: 0
    Offset: 209
Message sent:
    Topic: "AdhikariTaniya-locations"
    Partition: 0
    Offset: 210
Message sent:
    Topic: "AdhikariTaniya-locations"
    Partition: 0
    Offset: 211
Message sent:
    Topic: "AdhikariTaniya-locations"
    Partition: 0
    Offset: 212
Message sent:
    Topic: "AdhikariTaniya-locations"
    Partition: 0
    Offset: 213
Message sent:
    Topic: "AdhikariTaniya-locations"
    Partition: 0
    Offset: 214
Message sent:
    Topic: "AdhikariTaniya-locations"
    Partition: 0
    Offset: 215
Message sent:
    Topic: "AdhikariTaniya-locations"
    Partition: 0
    Offset: 216
Message sent:
    Topic: "AdhikariTaniya-location

Message sent:
    Topic: "AdhikariTaniya-locations"
    Partition: 0
    Offset: 303
Message sent:
    Topic: "AdhikariTaniya-locations"
    Partition: 0
    Offset: 304
Message sent:
    Topic: "AdhikariTaniya-locations"
    Partition: 0
    Offset: 305
Message sent:
    Topic: "AdhikariTaniya-locations"
    Partition: 0
    Offset: 306
Message sent:
    Topic: "AdhikariTaniya-locations"
    Partition: 0
    Offset: 307
Message sent:
    Topic: "AdhikariTaniya-locations"
    Partition: 0
    Offset: 308
Message sent:
    Topic: "AdhikariTaniya-locations"
    Partition: 0
    Offset: 309
Message sent:
    Topic: "AdhikariTaniya-locations"
    Partition: 0
    Offset: 310
Message sent:
    Topic: "AdhikariTaniya-locations"
    Partition: 0
    Offset: 311
Message sent:
    Topic: "AdhikariTaniya-locations"
    Partition: 0
    Offset: 312
Message sent:
    Topic: "AdhikariTaniya-locations"
    Partition: 0
    Offset: 313
Message sent:
    Topic: "AdhikariTaniya-locations"
    Partition

    Offset: 401
Message sent:
    Topic: "AdhikariTaniya-locations"
    Partition: 0
    Offset: 402
Message sent:
    Topic: "AdhikariTaniya-locations"
    Partition: 0
    Offset: 403
Message sent:
    Topic: "AdhikariTaniya-locations"
    Partition: 0
    Offset: 404
Message sent:
    Topic: "AdhikariTaniya-locations"
    Partition: 0
    Offset: 405
Message sent:
    Topic: "AdhikariTaniya-locations"
    Partition: 0
    Offset: 406
Message sent:
    Topic: "AdhikariTaniya-locations"
    Partition: 0
    Offset: 407
Message sent:
    Topic: "AdhikariTaniya-locations"
    Partition: 0
    Offset: 408
Message sent:
    Topic: "AdhikariTaniya-locations"
    Partition: 0
    Offset: 409
Message sent:
    Topic: "AdhikariTaniya-locations"
    Partition: 0
    Offset: 410
Message sent:
    Topic: "AdhikariTaniya-locations"
    Partition: 0
    Offset: 411
Message sent:
    Topic: "AdhikariTaniya-locations"
    Partition: 0
    Offset: 412
Message sent:
    Topic: "AdhikariTaniya-location

In [29]:
# publishing accelerations data
last_offset = 0
for index,row in accelerations.iterrows():
    offset = row['offset']
    time.sleep(offset - last_offset)
    payload = accelerations_dict[index]
    send_data('accelerations', payload)
    last_offset = offset

Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0
    Offset: 3
Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0
    Offset: 4
Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0
    Offset: 5
Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0
    Offset: 6
Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0
    Offset: 7
Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0
    Offset: 8
Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0
    Offset: 9
Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0
    Offset: 10
Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0
    Offset: 11
Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0
    Offset: 12
Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0
    Offset: 13
Message sent:
    Topic: "AdhikariTaniy

Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0
    Offset: 99
Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0
    Offset: 100
Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0
    Offset: 101
Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0
    Offset: 102
Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0
    Offset: 103
Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0
    Offset: 104
Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0
    Offset: 105
Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0
    Offset: 106
Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0
    Offset: 107
Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0
    Offset: 108
Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0
    Offset: 109
Message sent:
    Topi

Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0
    Offset: 197
Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0
    Offset: 198
Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0
    Offset: 199
Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0
    Offset: 200
Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0
    Offset: 201
Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0
    Offset: 202
Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0
    Offset: 203
Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0
    Offset: 204
Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0
    Offset: 205
Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0
    Offset: 206
Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0
    Offset: 207
Message sent:
    Top

Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0
    Offset: 293
Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0
    Offset: 294
Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0
    Offset: 295
Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0
    Offset: 296
Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0
    Offset: 297
Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0
    Offset: 298
Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0
    Offset: 299
Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0
    Offset: 300
Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0
    Offset: 301
Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0
    Offset: 302
Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0
    Offset: 303
Message sent:
    Top

Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0
    Offset: 397
Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0
    Offset: 398
Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0
    Offset: 399
Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0
    Offset: 400
Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0
    Offset: 401
Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0
    Offset: 402
Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0
    Offset: 403
Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0
    Offset: 404
Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0
    Offset: 405
Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0
    Offset: 406
Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0
    Offset: 407
Message sent:
    Top

...

    Offset: 23098
Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0
    Offset: 23099
Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0
    Offset: 23100
Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0
    Offset: 23101
Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0
    Offset: 23102
Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0
    Offset: 23103
Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0
    Offset: 23104
Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0
    Offset: 23105
Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0
    Offset: 23106
Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0
    Offset: 23107
Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0
    Offset: 23108
Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0

    Offset: 23198
Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0
    Offset: 23199
Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0
    Offset: 23200
Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0
    Offset: 23201
Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0
    Offset: 23202
Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0
    Offset: 23203
Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0
    Offset: 23204
Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0
    Offset: 23205
Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0
    Offset: 23206
Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0
    Offset: 23207
Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0
    Offset: 23208
Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0

Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0
    Offset: 23298
Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0
    Offset: 23299
Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0
    Offset: 23300
Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0
    Offset: 23301
Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0
    Offset: 23302
Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0
    Offset: 23303
Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0
    Offset: 23304
Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0
    Offset: 23305
Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0
    Offset: 23306
Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0
    Offset: 23307
Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0
    Offset: 23308

    Offset: 23400
Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0
    Offset: 23401
Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0
    Offset: 23402
Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0
    Offset: 23403
Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0
    Offset: 23404
Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0
    Offset: 23405
Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0
    Offset: 23406
Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0
    Offset: 23407
Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0
    Offset: 23408
Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0
    Offset: 23409
Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0
    Offset: 23410
Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0

Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0
    Offset: 23500
Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0
    Offset: 23501
Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0
    Offset: 23502
Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0
    Offset: 23503
Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0
    Offset: 23504
Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0
    Offset: 23505
Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0
    Offset: 23506
Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0
    Offset: 23507
Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0
    Offset: 23508
Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0
    Offset: 23509
Message sent:
    Topic: "AdhikariTaniya-accelerations"
    Partition: 0
    Offset: 23510

In [30]:
import json

from kafka import KafkaConsumer

### Configuration Parameters 

> **TODO:** Change the configuration prameters to the appropriate values for your setup.

In [31]:
config = dict(
    bootstrap_servers=['localhost:9092'],
    first_name='Taniya',
    last_name='Adhikari'
)

config['client_id'] = '{}{}'.format(
    config['last_name'], 
    config['first_name']
)
config['topic_prefix'] = '{}{}'.format(
    config['last_name'], 
    config['first_name']
)

config

{'bootstrap_servers': ['localhost:9092'],
 'first_name': 'Taniya',
 'last_name': 'Adhikari',
 'client_id': 'AdhikariTaniya',
 'topic_prefix': 'AdhikariTaniya'}

Create a consumer without subscribing to any particular topic

In [32]:
general_consumer = KafkaConsumer(
    bootstrap_servers=config['bootstrap_servers']
)

List all topics you are currently allowed to view

In [33]:
general_consumer.topics()

{'AdhikariTaniya-accelerations', 'AdhikariTaniya-locations'}

Close the consumer, waiting indefinitely for any needed cleanup.

In [34]:
general_consumer.close()

In [36]:
def create_kafka_consumer(topics, config=config):
    bootstrap_servers = config['bootstrap_servers']
    client_id = config['client_id']
    topic_prefix = config['topic_prefix']    
    topic_list = ['{}-{}'.format(topic_prefix, topic) for topic in topics]
    
    return KafkaConsumer(
        *topic_list,
        client_id=client_id,
        bootstrap_servers=bootstrap_servers,
        auto_offset_reset='earliest',
        enable_auto_commit=False,
        value_deserializer=lambda x: json.loads(x)
    )

consumer = create_kafka_consumer(['locations', 'accelerations'])

Gets a list of this consumer's current subscriptions

In [37]:
consumer.subscription()

{'AdhikariTaniya-accelerations', 'AdhikariTaniya-locations'}

The following function prints messages from the current consumer subscriptions. It will continue until manually stopped. 

In [38]:
def print_messages(consumer=consumer):
    try:
        for message in consumer:
                msg_metadata = 'Message metadata: {}:{}:{}'.format(
                    message.topic, message.partition, message.offset
                )

                if message.key is not None:
                    msg_key = message.key.decode('utf-8')
                else:
                    msg_key = ''
                msg_value = json.dumps(message.value, indent=2)
                msg_value = '\n'.join(['  {}'.format(value) for value in msg_value.split('\n')])

                print('Message metadata:')
                print('  Topic: {}'.format(message.topic))
                print('  Partition: {}'.format(message.partition))
                print('  Offset: {}'.format(message.offset))
                print('Message Key: {}'.format(msg_key))
                print('Message Value:')
                print(msg_value)
                print()
    except KeyboardInterrupt:
        print("STOPPING MESSAGE CONSUMER")
        
print_messages()

Message metadata:
  Topic: AdhikariTaniya-accelerations
  Partition: 0
  Offset: 0
Message Key: df20dd5175a04f13987224ef91aea318
Message Value:
  {
    "key1": "value1",
    "key2": "value2"
  }

Message metadata:
  Topic: AdhikariTaniya-accelerations
  Partition: 0
  Offset: 1
Message Key: 5b865b614e7c426191b686e37b8c9823
Message Value:
  {
    "key1": "value1",
    "key2": "value2"
  }

Message metadata:
  Topic: AdhikariTaniya-accelerations
  Partition: 0
  Offset: 2
Message Key: d893392e63bc49f68ed440866038d828
Message Value:
  {
    "key1": "value1",
    "key2": "value2"
  }

Message metadata:
  Topic: AdhikariTaniya-accelerations
  Partition: 0
  Offset: 3
Message Key: cca1d6387f8441efa32492787515b741
Message Value:
  {
    "index": 0,
    "id": "58682c5d48cad9d9e103431d773615bf",
    "ride_id": "c9a2b46c9aa515b632eddc45c4868482",
    "uuid": "19b9aa10588646b3bf22c9b4865a7995",
    "timestamp": "1970-01-01 00:25:03.882586",
    "offset": 0.8220608865228429,
    "x": -0.994,
    "

  Offset: 281
Message Key: 29a6d69f043a451c85ecd199d54a1515
Message Value:
  {
    "index": 266,
    "id": "58682c5d48cad9d9e103431d773615bf",
    "ride_id": "c9a2b46c9aa515b632eddc45c4868482",
    "uuid": "19b9aa10588646b3bf22c9b4865a7995",
    "timestamp": "1970-01-01 00:25:03.882576",
    "offset": 10.846060886522842,
    "x": -1.014,
    "y": 0.063,
    "z": -0.07200000000000001,
    "timelapse": false,
    "filename": "e2f795a7-6a7d-4500-b5d7-4569de996811.mov",
    "t": "010.6"
  }

Message metadata:
  Topic: AdhikariTaniya-accelerations
  Partition: 0
  Offset: 282
Message Key: ea0fc0cc74094c28863cc2848c37b131
Message Value:
  {
    "index": 346,
    "id": "85c61911b7fe2ced1000c33c9e932706",
    "ride_id": "6760ffa3f41908695d1405b776c3e8d5",
    "uuid": "dad7eae44e784b549c8c5a3aa051a8c7",
    "timestamp": "1970-01-01 00:25:07.320443",
    "offset": 10.846912529556645,
    "x": -1.052,
    "y": -0.11900000000000001,
    "z": -0.10200000000000001,
    "timelapse": false,
    "filen

  Offset: 561
Message Key: f405cfc6454745409d9d4f73484d5903
Message Value:
  {
    "index": 586,
    "id": "85c61911b7fe2ced1000c33c9e932706",
    "ride_id": "6760ffa3f41908695d1405b776c3e8d5",
    "uuid": "dad7eae44e784b549c8c5a3aa051a8c7",
    "timestamp": "1970-01-01 00:25:07.320435",
    "offset": 18.107912529556646,
    "x": -0.974,
    "y": 0.081,
    "z": 0.167,
    "timelapse": false,
    "filename": "d745b92f-aefd-467d-9121-7a71308e8d6d.mov",
    "t": "017.9"
  }

Message metadata:
  Topic: AdhikariTaniya-accelerations
  Partition: 0
  Offset: 562
Message Key: 597979b85a9c4dc2899e0197009cd62c
Message Value:
  {
    "index": 548,
    "id": "58682c5d48cad9d9e103431d773615bf",
    "ride_id": "c9a2b46c9aa515b632eddc45c4868482",
    "uuid": "19b9aa10588646b3bf22c9b4865a7995",
    "timestamp": "1970-01-01 00:25:03.882569",
    "offset": 18.12406088652284,
    "x": -0.989,
    "y": -0.11,
    "z": 0.113,
    "timelapse": false,
    "filename": "e2f795a7-6a7d-4500-b5d7-4569de996811.mo

Message Key: ab54643ee7c14d69afd6783bd87a1de1
Message Value:
  {
    "index": 844,
    "id": "85c61911b7fe2ced1000c33c9e932706",
    "ride_id": "6760ffa3f41908695d1405b776c3e8d5",
    "uuid": "dad7eae44e784b549c8c5a3aa051a8c7",
    "timestamp": "1970-01-01 00:25:07.320427",
    "offset": 26.50191252955665,
    "x": -1.051,
    "y": -0.02,
    "z": 0.028,
    "timelapse": false,
    "filename": "d745b92f-aefd-467d-9121-7a71308e8d6d.mov",
    "t": "026.1"
  }

Message metadata:
  Topic: AdhikariTaniya-accelerations
  Partition: 0
  Offset: 800
Message Key: 89a07b3f69314a668b23dd366f9f1c30
Message Value:
  {
    "index": 776,
    "id": "58682c5d48cad9d9e103431d773615bf",
    "ride_id": "c9a2b46c9aa515b632eddc45c4868482",
    "uuid": "19b9aa10588646b3bf22c9b4865a7995",
    "timestamp": "1970-01-01 00:25:03.882561",
    "offset": 26.50406088652284,
    "x": -1.238,
    "y": 0.158,
    "z": -0.008,
    "timelapse": false,
    "filename": "e2f795a7-6a7d-4500-b5d7-4569de996811.mov",
    "t": "

  Offset: 1050
Message Key: b82e20c682c4440a9c2250036905a492
Message Value:
  {
    "index": 969,
    "id": "58682c5d48cad9d9e103431d773615bf",
    "ride_id": "c9a2b46c9aa515b632eddc45c4868482",
    "uuid": "19b9aa10588646b3bf22c9b4865a7995",
    "timestamp": "1970-01-01 00:25:03.882555",
    "offset": 31.957060886522843,
    "x": -1.083,
    "y": 0.10300000000000001,
    "z": 0.179,
    "timelapse": false,
    "filename": "e2f795a7-6a7d-4500-b5d7-4569de996811.mov",
    "t": "030.4"
  }

Message metadata:
  Topic: AdhikariTaniya-accelerations
  Partition: 0
  Offset: 1051
Message Key: 3b282abe7a8c43659ca3a7cdf8f755c1
Message Value:
  {
    "index": 1053,
    "id": "85c61911b7fe2ced1000c33c9e932706",
    "ride_id": "6760ffa3f41908695d1405b776c3e8d5",
    "uuid": "dad7eae44e784b549c8c5a3aa051a8c7",
    "timestamp": "1970-01-01 00:25:07.320422",
    "offset": 31.968912529556647,
    "x": -1.032,
    "y": -0.022,
    "z": 0.068,
    "timelapse": false,
    "filename": "d745b92f-aefd-467d-9

...


Message metadata:
  Topic: AdhikariTaniya-accelerations
  Partition: 0
  Offset: 5879
Message Key: 8ba93274b95546b2bed0018e5c0b1166
Message Value:
  {
    "index": 5963,
    "id": "c44516bd325cb60548b431b4d6409dde",
    "ride_id": "b063cb65cd8446b83b4a09d4db2646c8",
    "uuid": "c6608d4cb9224aa3a0763a835e6c8788",
    "timestamp": "1970-01-01 00:25:06.796320",
    "offset": 61.0797702566351,
    "x": -0.973,
    "y": 0.025,
    "z": 0.085,
    "timelapse": false,
    "filename": "0d4d27dc-360b-4bb2-9b0c-bf84be964785.mov",
    "t": "060.1"
  }

Message metadata:
  Topic: AdhikariTaniya-accelerations
  Partition: 0
  Offset: 5880
Message Key: deb2357a0ab245758fa676ade1f3a8a3
Message Value:
  {
    "index": 5805,
    "id": "097ec0c2d59a23b76b4942bd8d9a7a77",
    "ride_id": "9cd83b5a569a73d2e596888b6a6ad6ad",
    "uuid": "a8fab740fe074ef1acc7d4c940398ce8",
    "timestamp": "1970-01-01 00:25:04.070053",
    "offset": 61.08229633059419,
    "x": 1.168,
    "y": 0.12,
    "z": 0.13,
    "time

  }

Message metadata:
  Topic: AdhikariTaniya-accelerations
  Partition: 0
  Offset: 6136
Message Key: ae49035e842547e2ab45f7721d962e15
Message Value:
  {
    "index": 6173,
    "id": "3b4793accf1f5feb077f7c8e097642a7",
    "ride_id": "5205b643b19fddd587541333533b2d4a",
    "uuid": "f547f4bf60cb40d3a86e00412d076e18",
    "timestamp": "1970-01-01 00:25:07.471323",
    "offset": 61.33891734364177,
    "x": 0.961,
    "y": 0.0,
    "z": -0.009000000000000001,
    "timelapse": false,
    "filename": "3fd49753-bc3e-401c-8511-bcb79223cc6b.mov",
    "t": "060.1"
  }

Message metadata:
  Topic: AdhikariTaniya-accelerations
  Partition: 0
  Offset: 6137
Message Key: 646721cf70f4469c8079a31e27ef405a
Message Value:
  {
    "index": 5818,
    "id": "097ec0c2d59a23b76b4942bd8d9a7a77",
    "ride_id": "9cd83b5a569a73d2e596888b6a6ad6ad",
    "uuid": "a8fab740fe074ef1acc7d4c940398ce8",
    "timestamp": "1970-01-01 00:25:04.070052",
    "offset": 61.342296330594195,
    "x": 1.014,
    "y": -0.07200000

  Offset: 6399
Message Key: b29edef33b92413296ab5f36153b0463
Message Value:
  {
    "index": 6938,
    "id": "f3134b3497ad6a52204ba8419d9000c5",
    "ride_id": "4611efd78aae450b1a506d67c4b71c17",
    "uuid": "9c8f3a88bdab444c92a4c7aab083704a",
    "timestamp": "1970-01-01 00:25:03.758598",
    "offset": 63.91328348917131,
    "x": 0.989,
    "y": 0.01,
    "z": -0.047,
    "timelapse": false,
    "filename": "be49d159-d750-4191-aba8-fa72218a78ca.mov",
    "t": "063.8"
  }

Message metadata:
  Topic: AdhikariTaniya-accelerations
  Partition: 0
  Offset: 6400
Message Key: 0e2d87d4765449b3ab87967c55e3850a
Message Value:
  {
    "index": 7323,
    "id": null,
    "ride_id": "2b03d428bd7d19d5f57d569571a15bf9",
    "uuid": "f1fb0285e0f444e99d00a563e52d8ad3",
    "timestamp": "1970-01-01 00:24:49.880984",
    "offset": 63.91341305234163,
    "x": 1.0070000000000001,
    "y": 0.002,
    "z": -0.017,
    "timelapse": false,
    "filename": "8abaa40f-7d6f-4391-9312-02a9dc8700cb.mov",
    "t": "0

  Partition: 0
  Offset: 6661
Message Key: 6914f6c00c444b64b31485739a784048
Message Value:
  {
    "index": 7335,
    "id": null,
    "ride_id": "2b03d428bd7d19d5f57d569571a15bf9",
    "uuid": "f1fb0285e0f444e99d00a563e52d8ad3",
    "timestamp": "1970-01-01 00:24:49.880984",
    "offset": 64.15241305234163,
    "x": 1.008,
    "y": 0.002,
    "z": -0.015,
    "timelapse": false,
    "filename": "8abaa40f-7d6f-4391-9312-02a9dc8700cb.mov",
    "t": "063.8"
  }

Message metadata:
  Topic: AdhikariTaniya-accelerations
  Partition: 0
  Offset: 6662
Message Key: 4f12781835c54da681f0484d49449807
Message Value:
  {
    "index": 6372,
    "id": null,
    "ride_id": "53a79e2d25ebf0ea29b4f4dea39496b3",
    "uuid": "080ab7e8d1bb4ac4bcf6b32bec82607d",
    "timestamp": "1970-01-01 00:24:50.366738",
    "offset": 64.1531238107275,
    "x": -1.115,
    "y": 0.155,
    "z": 0.063,
    "timelapse": false,
    "filename": "b0c74075-f0c0-470a-a2bf-c627f91b30b6.mov",
    "t": "063.8"
  }

Message metadata:

  }

Message metadata:
  Topic: AdhikariTaniya-accelerations
  Partition: 0
  Offset: 6919
Message Key: e7b1729135ed4342b11179f678066309
Message Value:
  {
    "index": 6659,
    "id": null,
    "ride_id": "582d3e7fa3cc301af55d6cb6bf20de0c",
    "uuid": "35a1f553cfa849bbaec122df745c9457",
    "timestamp": "1970-01-01 00:24:50.662675",
    "offset": 64.38398862018565,
    "x": -0.977,
    "y": 0.017,
    "z": -0.009000000000000001,
    "timelapse": false,
    "filename": "e9ac52ac-7ccd-48a5-af60-7bdd8c53ac9f.mov",
    "t": "063.8"
  }

Message metadata:
  Topic: AdhikariTaniya-accelerations
  Partition: 0
  Offset: 6920
Message Key: b14ca697afc742369ca5069f4d8233d2
Message Value:
  {
    "index": 6742,
    "id": null,
    "ride_id": "9193dfcf9af8e291e9aec60323f85646",
    "uuid": "72816a834e6e45a0812b7d81177b04a7",
    "timestamp": "1970-01-01 00:24:50.651506",
    "offset": 64.38460457626101,
    "x": -1.062,
    "y": 0.124,
    "z": 0.038,
    "timelapse": false,
    "filename": "8248

Close the consumer, waiting indefinitely for any needed cleanup.

In [39]:
consumer.close()